In [68]:
!pip install osmnx geopandas shapely pandas pyproj scikit-learn matplotlib folium hdbscan geopy meteostat


[notice] A new release of pip is available: 24.3.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [69]:
# Importar librerías necesarias
import osmnx as ox
import geopandas as gpd
import pandas as pd
from shapely.geometry import Point
from pyproj import Transformer

import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import DBSCAN
import matplotlib.pyplot as plt

In [70]:
accidentes = pd.read_csv('../../2024_Accidentalidad.csv', sep=";")

# Verificar las columnas disponibles
print(accidentes.columns)
print(accidentes.head())

Index(['num_expediente', 'fecha', 'hora', 'localizacion', 'numero',
       'cod_distrito', 'distrito', 'tipo_accidente', 'estado_meteorológico',
       'tipo_vehiculo', 'tipo_persona', 'rango_edad', 'sexo', 'cod_lesividad',
       'lesividad', 'coordenada_x_utm', 'coordenada_y_utm', 'positiva_alcohol',
       'positiva_droga'],
      dtype='object')
  num_expediente       fecha      hora  \
0    2023S040280  04/01/2024  14:09:00   
1    2023S040280  04/01/2024  14:09:00   
2    2023S040309  15/02/2024  14:05:00   
3    2023S040309  15/02/2024  14:05:00   
4    2023S040310  18/02/2024  10:40:00   

                               localizacion numero  cod_distrito   distrito  \
0  AVDA. NICETO ALCALA ZAMORA / AUTOV. M-11      3            16  HORTALEZA   
1  AVDA. NICETO ALCALA ZAMORA / AUTOV. M-11      3            16  HORTALEZA   
2                CALL. TESORO / CALL. MINAS     18             1     CENTRO   
3                CALL. TESORO / CALL. MINAS     18             1     CENTRO   


In [71]:
# Crear un transformador para convertir de UTM Zona 30 a WGS84
transformer = Transformer.from_crs("EPSG:25830", "EPSG:4326", always_xy=True)

# Función para convertir coordenadas UTM a Lat/Lon
def utm_to_latlon(row):
    if pd.notnull(row["coordenada_x_utm"]) and pd.notnull(row["coordenada_y_utm"]):
        lon, lat = transformer.transform(row["coordenada_x_utm"], row["coordenada_y_utm"])
        return pd.Series([lat, lon])
    else:
        return pd.Series([None, None])

# Aplicar la conversión en nuevas columnas
accidentes[["latitud", "longitud"]] = accidentes.apply(utm_to_latlon, axis=1)

# Verificar que las nuevas columnas existen
print(accidentes[["latitud", "longitud"]].head())


     latitud  longitud
0  40.481706 -3.649939
1  40.481706 -3.649939
2  40.425009 -3.705860
3  40.425009 -3.705860
4  40.429974 -3.705746


In [72]:
# Eliminar filas con valores NaN en latitud o longitud
accidentes = accidentes.dropna(subset=["latitud", "longitud"])

# Crear geometría de puntos
accidentes["geometry"] = accidentes.apply(lambda row: Point(row["longitud"], row["latitud"]), axis=1)

# Convertir a GeoDataFrame con CRS WGS84
accidentes_gdf = gpd.GeoDataFrame(accidentes, geometry="geometry", crs="EPSG:4326")

# Mostrar los primeros datos transformados
print(accidentes_gdf.head())


  num_expediente       fecha      hora  \
0    2023S040280  04/01/2024  14:09:00   
1    2023S040280  04/01/2024  14:09:00   
2    2023S040309  15/02/2024  14:05:00   
3    2023S040309  15/02/2024  14:05:00   
4    2023S040310  18/02/2024  10:40:00   

                               localizacion numero  cod_distrito   distrito  \
0  AVDA. NICETO ALCALA ZAMORA / AUTOV. M-11      3            16  HORTALEZA   
1  AVDA. NICETO ALCALA ZAMORA / AUTOV. M-11      3            16  HORTALEZA   
2                CALL. TESORO / CALL. MINAS     18             1     CENTRO   
3                CALL. TESORO / CALL. MINAS     18             1     CENTRO   
4    GTA. RUIZ JIMENEZ / CALL. SAN BERNARDO      3             7   CHAMBERÍ   

            tipo_accidente estado_meteorológico            tipo_vehiculo  ...  \
0  Colisión fronto-lateral         Lluvia débil      Motocicleta > 125cc  ...   
1  Colisión fronto-lateral         Lluvia débil                  Turismo  ...   
2  Colisión fronto-lateral   

In [73]:
df = accidentes_gdf

In [74]:
# Antes de formatear la localizacion vamos a ver que forma tiene para saber como hacer la limpieza

df["localizacion"].dropna().sample(10, random_state=42).tolist()


['AUTOV. M-30, 20XC00',
 'CALL. OLVEGA, 26',
 'AUTOV. A-2, +00500E',
 'GTA. BILBAO / CALL. FUENCARRAL',
 'CALL. DOCTOR RAMON CASTROVIEJO / GTA. MARIANO SALVADOR MAELLA',
 'CALL. PEÑARANDA DE BRACAMONTE, 20A',
 "CALL. O'DONNELL, 21",
 'PLAZA. CONDE DE CASAL / CALL. CARLOS Y GUILLERMO FERNANDEZ SHAW',
 'AVDA. ENSANCHE DE VALLECAS / AUTOV. M-45',
 'CALL. SANTISIMA TRINIDAD / CALL. VIRIATO']

In [75]:
!pip install unidecode



[notice] A new release of pip is available: 24.3.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [76]:
import re
from unidecode import unidecode

def clean_localizacion(texto):
    if pd.isna(texto):
        return ""
    texto = unidecode(texto.lower())  # ✅ Solo la función
    texto = re.sub(r"[^a-z\s]", "", texto)
    texto = re.sub(r"\s+", " ", texto).strip()
    return texto


def refinar_localizacion_limpia(texto):
    # Aquí puedes añadir lógica personalizada, por ejemplo:
    # Cambiar abreviaturas, corregir errores comunes, etc.
    # Este ejemplo es muy básico:
    reemplazos = {
        "avda": "avenida",
        "c": "calle",
        "pz": "plaza",
    }
    palabras = texto.split()
    palabras_refinadas = [reemplazos.get(p, p) for p in palabras]
    return " ".join(palabras_refinadas)


def refinar_lista_calles(lista_calles):
    if not isinstance(lista_calles, list):
        return []
    return [refinar_localizacion_limpia(calle) for calle in lista_calles]



In [77]:
import pandas as pd
import numpy as np
import hdbscan
from sklearn.preprocessing import StandardScaler

# Asegurarse de que la columna 'hora' esté en formato datetime
df['hora'] = pd.to_datetime(df['hora'], format='%H:%M:%S')

# Convertir la hora a minutos desde medianoche
df['hora_minutos'] = df['hora'].dt.hour * 60 + df['hora'].dt.minute

# Filtrar filas con coordenadas NaN
df = df.dropna(subset=["latitud", "longitud", "hora_minutos"])

df["localizacion_limpia"] = df["localizacion"].apply(clean_localizacion)
df["localizacion_limpia"] = df["localizacion_limpia"].apply(refinar_localizacion_limpia)


# Convertir las coordenadas geográficas (latitud, longitud) a radianes
coords_geo = np.radians(df[["latitud", "longitud"]].values)

# Aplicar HDBSCAN con la métrica 'haversine' para las coordenadas geográficas
clusterer = hdbscan.HDBSCAN(min_cluster_size=10, metric="haversine")
cluster_labels = clusterer.fit_predict(coords_geo)

# Guardar los clusters en el DataFrame
df["cluster"] = cluster_labels

# Crear un resumen de los clusters (sin hora en la métrica)
df_cluster = df.groupby("cluster").agg(
    num_elementos=("cluster", "count"),
    media_latitud=("latitud", "mean"),
    media_longitud=("longitud", "mean"),
    max_hora=("hora_minutos", "max"),
    min_hora=("hora_minutos", "min")
).reset_index()

# Eliminar el cluster -1 (puntos considerados ruido)
df_cluster = df_cluster[df_cluster["cluster"] != -1]
# Añadir la lista de localizaciones por cluster
loc_por_cluster = df[df["cluster"] != -1].groupby("cluster")["localizacion_limpia"].apply(list).reset_index()
df_cluster = df_cluster.merge(loc_por_cluster, on="cluster")


df_cluster.head()




c:\Users\thelu\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\thelu\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


cluster  num_elementos  media_latitud  media_longitud  max_hora  min_hora  \
0        0             13      40.517878       -3.775513      1335        30   
1        1             13      40.428560       -3.576810      1075       855   
2        2             25      40.427044       -3.579117      1240       420   
3        3             51      40.353118       -3.570552      1270        45   
4        4             10      40.462859       -3.770520      1410       580   

                                 localizacion_limpia  
0  [ctra m s, call guardia civil, call guardia ci...  
1  [ctra vicalvaro a coslada avenida marconi, ctr...  
2  [avenida arcentales avenida marconi, avenida a...  
3  [m km km via servicio, m km km via servicio, m...  
4  [autov m autov a, autov m autov a, autov m aut...

In [78]:
df_cluster.size

10283

In [79]:
import pandas as pd
import re
from unidecode import unidecode

def refinar_localizacion_limpia(lista_calles):
    if not isinstance(lista_calles, list):
        return []

    clean_list = []
    replacements = {
        "c,": "calle",
        "c.": "calle",
        "ctra.": "carretera",
        "inter.": "",
        "idb.": "",
        "pk": "",
        "s/n": "",
        "km": "",
        "p.k.": "",
        "autov.": "autovia",
        "av.": "avenida"
    }

    for entrada in lista_calles:
        # Si es una lista anidada (como [["calle a, calle b"]])
        if isinstance(entrada, list):
            subcalles = entrada
        else:
            subcalles = [entrada]

        for calle in subcalles:
            calle = calle.lower()
            calle = unidecode(calle)

            # Reemplazos
            for abbr, full in replacements.items():
                calle = calle.replace(abbr, full)

            # Eliminar caracteres raros
            calle = re.sub(r"[^a-z0-9áéíóúüñ ]", " ", calle)
            calle = re.sub(r"\s+", " ", calle).strip()

            # Evitar vacíos
            if calle and calle not in clean_list:
                clean_list.append(calle)

    return clean_list
    



In [80]:
df_cluster["localizacion_limpia"] = df_cluster["localizacion_limpia"].apply(refinar_localizacion_limpia)


In [81]:
!pip install haversine


[notice] A new release of pip is available: 24.3.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [82]:
from haversine import haversine

def merge_close_clusters(df_cluster, distance_threshold_meters=20):
    merged_clusters = []
    visited = set()
    
    for idx, row in df_cluster.iterrows():
        if row["cluster"] in visited:
            continue

        group = [row["cluster"]]
        lat1, lon1 = row["media_latitud"], row["media_longitud"]

        for jdx, other in df_cluster.iterrows():
            if other["cluster"] in visited or other["cluster"] == row["cluster"]:
                continue

            lat2, lon2 = other["media_latitud"], other["media_longitud"]
            distance = haversine((lat1, lon1), (lat2, lon2)) * 1000  # Convert km to meters

            if distance < distance_threshold_meters:
                group.append(other["cluster"])
                visited.add(other["cluster"])

        # Agrega el cluster principal también
        visited.update(group)

        # Extrae y combina la info de todos los clusters del grupo
        sub_df = df_cluster[df_cluster["cluster"].isin(group)]

        merged_clusters.append({
            "cluster": min(group),
            "num_elementos": sub_df["num_elementos"].sum(),
            "media_latitud": sub_df["media_latitud"].mean(),
            "media_longitud": sub_df["media_longitud"].mean(),
            "max_hora": sub_df["max_hora"].max(),
            "min_hora": sub_df["min_hora"].min(),
            "localizacion_limpia": sum(sub_df["localizacion_limpia"], [])
        })

    return pd.DataFrame(merged_clusters)


In [83]:
df_cluster_merged = merge_close_clusters(df_cluster)

In [84]:
df_cluster_merged.size

10220

In [85]:
!pip install openpyxl



[notice] A new release of pip is available: 24.3.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [86]:
df_estaciones = pd.read_excel('../Originales/ubicaciones trafico/pmed_ubicacion_10-2024.xlsx')

In [87]:
df_estaciones.head()

tipo_elem  distrito     id cod_cent                                  nombre  \
0       URB      11.0   5094    50404                 (TACTICO) GUADALETE E-O   
1       URB      11.0   3551    50406                 (TACTICO) NAVAHONDA O-E   
2       URB      11.0  11314    50407            (TACTICO) MIGUEL SORIANO E-O   
3       URB      11.0   5139    58008  PORTALEGRE O-E ENTRE OPORTO Y ABRANTES   
4       URB      11.0   5140    58009  FARO E-O ENTRE VÍA LUSITANA Y ABRANTES   

           utm_x         utm_y  longitud    latitud  
0  439225.835430  4.471196e+06 -3.716056  40.389144  
1  439283.029354  4.471616e+06 -3.715422  40.392933  
2  439305.621686  4.471490e+06 -3.715144  40.391797  
3  438562.312598  4.470700e+06 -3.723825  40.384629  
4  438377.184286  4.470303e+06 -3.725967  40.381038

## Limpieza nombre df_estaciones

In [183]:
def clean_nombre_estacion(nombre):
    if pd.isna(nombre):
        return ""

    nombre = nombre.upper()

    # Eliminar textos entre paréntesis
    nombre = re.sub(r"\s+", " ", nombre).strip()

    nombre = re.sub(r"\b(pm\d{5}|cta|paseo|avda|glorieta|plaza)\b", "", nombre)  # quitar ruido
    nombre = re.sub(r"\b(m[\s-]?30|autovía m30|avenida paz)\b", "m30", nombre)
    nombre = re.sub(r"\s+", " ", nombre).strip()

    # Reemplazos comunes (igual que antes)
    replacements = {
        "CALL.": "calle",
        "AVDA.": "avenida",
        "AVD.": "avenida",
        "GTA.": "glorieta",
        "GLTA.": "glorieta",
        "PLAZA.": "plaza",
        "PLZA.": "plaza",
        "AUTOV.": "autovia",
        "PASEO.": "paseo",
        "BULEV.": "bulevar"
    }

    for abbr, full in replacements.items():
        nombre = nombre.replace(abbr, full)

    # Eliminar palabras y patrones irrelevantes
    eliminar = [
        "SALIDA", "ENTRADA", "GIRO", "IZDA", "DCHA", "IZQUIERDA", "DERECHA",
        "PK", "P.K.", "KM", "M-", "N-", "OESTE", "ESTE", "NORTE", "SUR"
    ]

    for palabra in eliminar:
        nombre = re.sub(rf"\b{palabra}\b", "", nombre)

    # Eliminar códigos (como o123, pm10021, etc.)
    nombre = re.sub(r"\b[a-zA-Z]{1,3}\d{2,5}\b", "", nombre)

    # Eliminar guiones múltiples y limpiar espacios
    nombre = nombre.replace("-", " ")
    nombre = re.sub(r"\s+", " ", nombre)
    nombre = unidecode(nombre.lower().strip())

    return nombre


In [89]:
df_estaciones["nombre_limpio"] = df_estaciones["nombre"].apply(clean_nombre_estacion)


In [90]:
from scipy.spatial import cKDTree

# Crear árbol KD con las coordenadas de las estaciones
tree = cKDTree(df_estaciones[["latitud", "longitud"]].values)

# Buscar la estación más cercana para cada cluster
distancias, indices = tree.query(df_cluster_merged[["media_latitud", "media_longitud"]].values)

# Agregar la columna con el ID de la estación más cercana
df_cluster_merged["id_estacion_proxima"] = df_estaciones.iloc[indices]["id"].values
df_cluster_merged["longitud_estacion"] = df_estaciones.iloc[indices]["longitud"].values
df_cluster_merged["latitud_estacion"] = df_estaciones.iloc[indices]["latitud"].values

# Solo columnas necesarias para el merge
df_estaciones_reducido = df_estaciones[["id", "nombre_limpio"]]

# Merge con df_cluster usando el ID de estación
# Volver a hacer merge para que tenga el nombre limpio actualizado
df_cluster_merged = df_cluster_merged.drop(columns=["nombre_estacion_proxima"], errors="ignore")

df_cluster_merged = df_cluster_merged.merge(
    df_estaciones[["id", "nombre_limpio"]],
    how="left",
    left_on="id_estacion_proxima",
    right_on="id"
).rename(columns={"nombre_limpio": "nombre_estacion_proxima"})


# Renombrar columna para más claridad
df_cluster_merged = df_cluster_merged.rename(columns={"nombre_limpio": "nombre_calle_estacion_proxima"})


print(df_cluster_merged.head())  # Ver resultado


   cluster  num_elementos  media_latitud  media_longitud  max_hora  min_hora  \
0        0             13      40.517878       -3.775513      1335        30   
1        1             13      40.428560       -3.576810      1075       855   
2        2             25      40.427044       -3.579117      1240       420   
3        3             51      40.353118       -3.570552      1270        45   
4        4             10      40.462859       -3.770520      1410       580   

                                 localizacion_limpia  id_estacion_proxima  \
0  [ctra m s, call guardia civil, call mira el ri...                 3680   
1  [ctra vicalvaro a coslada avenida marconi, gta...                 6548   
2  [avenida arcentales avenida marconi, avenida a...                 6548   
3  [m via servicio, lugar canada real frente al n...                 5380   
4  [autov m autov a, avenida valdemarin call arge...                 4890   

   longitud_estacion  latitud_estacion    id  \
0       

In [91]:
!pip install rapidfuzz


[notice] A new release of pip is available: 24.3.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [92]:
from rapidfuzz import fuzz

def best_matching_score_v3(row):
    # Prepara nombre de estación
    nombre_estacion = row["nombre_estacion_proxima"]
    if pd.isna(nombre_estacion):
        return 0

    nombre_estacion = unidecode(nombre_estacion.lower())
    nombre_estacion = re.sub(r"\(.*?\)", "", nombre_estacion)
    nombre_estacion = re.sub(r"\b(?:s\.?n\.?|e\s?o|norte|sur|este|oeste|frente|delante|tactico|alde\.?|pm\d+)\b", "", nombre_estacion)
    partes_estacion = [p.strip() for p in re.split(r"[-,/]", nombre_estacion) if p.strip()]

    # Asegura que las calles sean una lista plana
    calles_cluster = row["localizacion_limpia"]
    if not calles_cluster or not isinstance(calles_cluster, list):
        return 0
    calles_flat = [item for sublist in calles_cluster for item in (sublist if isinstance(sublist, list) else [sublist])]

    # Comparar cada parte de la estación contra cada calle
    scores = []
    for parte in partes_estacion:
        for calle in calles_flat:
            calle = unidecode(calle.lower())
            s1 = fuzz.token_set_ratio(parte, calle)
            s2 = fuzz.partial_ratio(parte, calle)
            scores.append(max(s1, s2))

    return max(scores) if scores else 0


In [93]:
df_cluster_merged["score_estacion_vs_calles"] = df_cluster_merged.apply(best_matching_score_v3, axis=1)


In [264]:
from rapidfuzz import fuzz

def best_matching_score_v4(row):
    nombre_estacion = row["nombre_estacion_mejor"]
    calles_cluster = row["localizacion_limpia"]

    if pd.isna(nombre_estacion) or not isinstance(calles_cluster, list):
        return 0

    nombre_estacion_limpia = limpiar_autovia(nombre_estacion)
    
    # Flatten calles del cluster
    calles_flat = [item for sublist in calles_cluster for item in (sublist if isinstance(sublist, list) else [sublist])]
    calles_limpias = [limpiar_autovia(c) for c in calles_flat if isinstance(c, str)]

    # BONUS: Si el nombre de la estación y alguna calle contienen "m30", forzamos buen score
    if "m30" in nombre_estacion_limpia:
        if any("m30" in calle for calle in calles_limpias):
            return 90

    # Comparación usando Fuzzy
    scores = []
    for parte in nombre_estacion_limpia.split():
        for calle in calles_limpias:
            s1 = fuzz.token_set_ratio(parte, calle)
            s2 = fuzz.partial_ratio(parte, calle)
            scores.append(max(s1, s2))

    return max(scores) if scores else 0


In [265]:
df_cluster_merged["score_estacion_nombre"] = df_cluster_merged.apply(best_matching_score_v4, axis=1)


In [266]:
df_cluster_merged["match_valido"] = (df_cluster_merged["score_estacion_nombre"] >= 75) | df_cluster_merged["es_autovia"]


In [267]:
import folium
from folium.plugins import MarkerCluster

points = df_cluster_merged[["media_latitud", "media_longitud"]].values.tolist()
points_estaciones = df_cluster_merged[["latitud_estacion", "longitud_estacion"]].values.tolist()

m = folium.Map(location=[40, 0], zoom_start=6)
for point in points:
  folium.CircleMarker( location=[point[0], point[1]], radius=5, color="red", fill=True, fill_color="red", popup='', ).add_to(m)
for point in points_estaciones:
  folium.CircleMarker( location=[point[0], point[1]], radius=5, color="green", fill=True, fill_color="green", popup='', ).add_to(m)
for point1,point2 in zip(points,points_estaciones):
  folium.PolyLine(locations=[point1,point2],color="blue").add_to(m)


In [268]:
df_cluster_merged[["cluster", "nombre_estacion_proxima", "localizacion_limpia", "score_estacion_vs_calles"]].sort_values("score_estacion_vs_calles", ascending=False).head(10)


cluster                            nombre_estacion_proxima  \
1459     1468                  alcala e o(pl. cibeles barquillo)   
169       169  collado tirobarra e o(moralzarzal av. ventisqu...   
980       982  pocastellana s raimundo fernandez villaverde n...   
970       972  (aforos) jose abascal, 44 o e fernandez de la ...   
133       133               acceso a 3 acceso a 3 av. democracia   
913       915       santa engracia, 103 s n ponzano jose abascal   
905       907  (aforos) francos rodriguez e o(lorenzana po di...   
279       279  avenida san luis eladio lopez vilches_julio da...   
898       900  (aforos) bravo murillo, 75 s cristobal bordiu ...   
895       897  eloy gonzalo, 24 o e trafalgar glorietapintor ...   

                                    localizacion_limpia  \
1459  [paseo prado plaza cibeles, paseo prado call a...   
169   [avenida ventisquero de la condesa, avenida ve...   
980   [paseo castellana call raimundo fernandez vill...   
970   [call jose abascal call modesto lafuente, call...   
133   [a, avenida democracia carretera de valencia, ...   
913   [call santa engracia, call santa engracia call...   
905   [call francos rodriguez, call ofelia nieto, ca...   
279   [call mesena, avenida san luis call cuevas del...   
898   [avenida filipinas, plaza juan zorrilla call b...   
895   [call eloy gonzalo call trafalgar, call eloy g...   

      score_estacion_vs_calles  
1459                     100.0  
169                      100.0  
980                      100.0  
970                      100.0  
133                      100.0  
913                      100.0  
905                      100.0  
279                      100.0  
898                      100.0  
895                      100.0

In [269]:
df_cluster_merged[df_cluster_merged["score_estacion_vs_calles"] < 50][["cluster", "nombre_estacion_proxima", "localizacion_limpia", "score_estacion_vs_calles"]].sample(10)


cluster                          nombre_estacion_proxima  \
572       574     francos rodriguez e o(margaritas jose calvo)   
1185     1189                                                    
607       609                   mauricio legendre s(30 viejas)   
7           7                            pruebas signals 99002   
625       627  arroyo media legua santa irene acceso o'donnell   
695       697        (tactico)eduardo morales s n(amistad oca)   
1294     1298                                                    
140       140                                       19xc40pm01   
725       727                  po sta. ma cabeza s n (lateral)   
795       797                                       12nc07pm01   

                                    localizacion_limpia  \
572   [call roman alonso call luis misson, call vill...   
1185  [autov m, m, m30, m30, m30 calle, m30, autov m...   
607                        [m30, m30, m30, m, m30, m30]   
7     [call simpatia avenida miguel delibes, autov m...   
625   [autov m autov m, autov m, autov m, autov m, a...   
695   [avenida nuestra senora de valvanera call aceu...   
1294                 [m30, autov m calle, m30 exterior]   
140                     [m, m30, m30, m, autov m calle]   
725   [avenida princesa juana de austria, autov a s,...   
795                           [avenida planetario, m30]   

      score_estacion_vs_calles  
572                  48.275862  
1185                  0.000000  
607                  42.857143  
7                    41.025641  
625                  46.153846  
695                  47.368421  
1294                  0.000000  
140                  33.333333  
725                  47.058824  
795                  33.333333

In [270]:
df["localizacion_limpia"] = df["localizacion"].apply(clean_localizacion)
df["localizacion_limpia"] = df["localizacion_limpia"].apply(refinar_localizacion_limpia)


In [271]:
df_cluster_merged[["cluster", "localizacion_limpia"]].sample(5)


cluster                                localizacion_limpia
379       380  [gta lozares avenida real de pinto, avenida re...
703       705  [avenida doctor arce call oria, avenida doctor...
1261     1265  [plaza manuel becerra call alcala, call alcala...
280       280  [call sinesio delgado, call sinesio delgado ca...
1061     1064  [call cea bermudez call gaztambide, call gazta...

In [272]:
df_cluster_merged[["nombre_estacion_proxima"]].drop_duplicates().sample(10)


nombre_estacion_proxima
292                   (tactico) av. rosales a 40 (gr 8)
356   av. canillejas a vicalvaro maria sevilla diago...
32     av. partenon via de dublin av. capital de espana
896   gral. martinez campos o e glorieta pintor soro...
332   av. canillejas a vicalvaro a suecia aquitania ...
855                conde de penalver s ayala hermosilla
803        cno. viejo leganes s n(radio gral. ricardos)
408   (tactico)cuart poblet o44 o e cuart poblet alh...
1326                    rafael riego s(delicias ancora)
548        alfonso xiii s n ramon y cajal pintor ribera

import re

def limpiar_autovia(nombre):
    if pd.isna(nombre):
        return ""
    nombre = unidecode(nombre.lower())
    # Normalizar variaciones de autovía y M-30
    nombre = re.sub(r"\bautov\.\b", "autovia", nombre)
    nombre = re.sub(r"\bm[\s\-]?30\b", "m30", nombre)  # Asegurarse de que m30 esté normalizado
    nombre = re.sub(r"\b(m-?30|m30|autovía m30|avenida de la paz)\b", "m30", nombre)  # Variaciones comunes
    nombre = re.sub(r"\b(pk|km|entrada|salida|calzada|lateral|interior|exterior|p\.k\.)\b", "", nombre)
    nombre = re.sub(r"\d+[a-z]*", "", nombre)
    nombre = re.sub(r"[^a-z0-9\s]", "", nombre)
    nombre = re.sub(r"\s+", " ", nombre).strip()
    return nombre


In [273]:
import re
from unidecode import unidecode

def limpiar_autovia(nombre):
    if pd.isna(nombre):
        return ""
    nombre = unidecode(nombre.lower())

    # Normalización explícita de formas de referirse a la M-30
    nombre = re.sub(r"\blateral\s+30\b", "m30", nombre)
    nombre = re.sub(r"\b30\s+[ns]\b", "m30", nombre)
    nombre = re.sub(r"\bm[\s\-]?30\b", "m30", nombre)
    nombre = re.sub(r"\bcalle\s+30\b", "m30", nombre)
    nombre = re.sub(r"\bavenida\s+de\s+la\s+paz\b", "m30", nombre)

    # Sustituir deformaciones comunes tipo 'autov m xl', 'autov. m xc'
    nombre = re.sub(r"\bautov(?:ia)?\.?\s*m\s*[a-z]{1,3}\b", "m30", nombre)
    nombre = re.sub(r"\bm\s*[a-z]{1,3}\b", "m30", nombre)

    # Eliminar términos que ensucian la coincidencia pero no aportan
    nombre = re.sub(r"\b(salida|entrada|calzada|int|interior|lateral|sentido|union|central|al|pk|km|p\.k\.)\b", "", nombre)

    # Eliminar duplicaciones: 'm30 m30' → 'm30'
    nombre = re.sub(r"(m30\s*){2,}", "m30", nombre)

    # Limpieza final de símbolos y espacios
    nombre = re.sub(r"[^a-z0-9\s]", "", nombre)
    nombre = re.sub(r"\s+", " ", nombre).strip()

    return nombre


In [274]:
def enriquecer_nombre_estacion(row):
    nombre = row["nombre"]
    lat, lon = row["latitud"], row["longitud"]

    # Si nombre es NaN, tratamos como no descriptivo
    if pd.isna(nombre):
        nombre = ""

    nombre = str(nombre).lower()

    # Si tiene formato de código (p.ej. PM20233 o 09nc51pm01)
    if re.fullmatch(r"pm\d{5}", nombre) or re.match(r"\d{2}[a-z]{2}\d{2}pm\d{2}", nombre):
        if 40.38 < lat < 40.49 and -3.74 < lon < -3.63:  # Aproximadamente zona M30
            return "estacion m30"
        else:
            return "estacion sin nombre"
    return nombre


# Aplicar al DataFrame de estaciones
df_estaciones["nombre_limpio"] = df_estaciones.apply(enriquecer_nombre_estacion, axis=1)
df_estaciones["nombre_limpio"] = df_estaciones["nombre_limpio"].apply(limpiar_autovia)


In [275]:
from scipy.spatial import cKDTree
from rapidfuzz import fuzz

def encontrar_mejor_estacion(cluster_row, estaciones_df, k=3):
    cluster_coord = [cluster_row["media_latitud"], cluster_row["media_longitud"]]
    tree = cKDTree(estaciones_df[["latitud", "longitud"]].values)
    dists, idxs = tree.query(cluster_coord, k=k)

    calles_cluster = cluster_row["localizacion_limpia"]
    if not calles_cluster:
        return None, None, 0

    # Flatten calles
    calles_flat = [item for sub in calles_cluster for item in (sub if isinstance(sub, list) else [sub])]
    calles_flat = [limpiar_autovia(c) for c in calles_flat]

    best_score = 0
    best_idx = None

    for i in range(k):
        est_row = estaciones_df.iloc[idxs[i]]
        nombre_est = limpiar_autovia(est_row["nombre_limpio"])
        for calle in calles_flat:
            score = fuzz.token_set_ratio(nombre_est, calle)
            if score > best_score:
                best_score = score
                best_idx = idxs[i]

    if best_idx is not None:
        est = estaciones_df.iloc[best_idx]
        return est["id"], est["latitud"], est["longitud"], est["nombre_limpio"], best_score
    else:
        return None, None, None, None, 0


In [276]:
# Prepara columnas
ids, lats, lons, nombres, scores = [], [], [], [], []

for _, row in df_cluster_merged.iterrows():
    id_est, lat, lon, nom, sc = encontrar_mejor_estacion(row, df_estaciones, k=3)
    ids.append(id_est)
    lats.append(lat)
    lons.append(lon)
    nombres.append(nom)
    scores.append(sc)

df_cluster_merged["id_estacion_mejor"] = ids
df_cluster_merged["latitud_estacion_mejor"] = lats
df_cluster_merged["longitud_estacion_mejor"] = lons
df_cluster_merged["nombre_estacion_mejor"] = nombres
df_cluster_merged["score_estacion_nombre"] = scores


In [277]:
from scipy.spatial import cKDTree

# Construye el árbol para búsqueda rápida de estaciones
est_coords = df_estaciones[["latitud", "longitud"]].values
est_tree = cKDTree(est_coords)

# Crea columna si no existe
if "asignacion_forzada" not in df_cluster_merged.columns:
    df_cluster_merged["asignacion_forzada"] = False

# Recorre los clusters para forzar asignación si es autovía y no tiene estación asignada
for i, row in df_cluster_merged.iterrows():
    if row["es_autovia"] and pd.isna(row["nombre_estacion_mejor"]):
        lat, lon = row["media_latitud"], row["media_longitud"]
        _, idx = est_tree.query([lat, lon])

        est = df_estaciones.iloc[idx]

        df_cluster_merged.at[i, "id_estacion_mejor"] = est["id"]
        df_cluster_merged.at[i, "latitud_estacion_mejor"] = est["latitud"]
        df_cluster_merged.at[i, "longitud_estacion_mejor"] = est["longitud"]
        # Fallback si nombre_limpio está vacío
        nombre_final = est["nombre_limpio"]
        if not nombre_final or pd.isna(nombre_final) or nombre_final.strip() == "":
            nombre_final = est["nombre"]  # Usa el original si está vacío

        df_cluster_merged.at[i, "nombre_estacion_mejor"] = nombre_final
        df_cluster_merged.at[i, "score_estacion_nombre"] = 0
        df_cluster_merged.at[i, "asignacion_forzada"] = True


In [278]:
# Esto lo hago porque antes las autovias no las detectaba bien por el nombre de calle y no hacian match

def contiene_autovia(calles):
    if not calles:
        return False
    autovias = ["m30", "m-30", "calle 30", "autovia m30", "avenida de la paz", "m40", "a42", "a2", "a5"]
    for sub in calles:
        for calle in (sub if isinstance(sub, list) else [sub]):
            calle_limpia = limpiar_autovia(calle)
            if any(a in calle_limpia for a in autovias):
                return True
    return False



df_cluster_merged["localizacion_limpia"] = df_cluster_merged["localizacion_limpia"].apply(
    lambda calles: [limpiar_autovia(c) for c in calles] if isinstance(calles, list) else []
)

df_cluster_merged["es_autovia"] = df_cluster_merged["localizacion_limpia"].apply(contiene_autovia)
df_cluster_merged["es_autovia_total"] = df_cluster_merged["es_autovia"] | df_cluster_merged["es_autovia_geo"]
df_cluster_merged["match_valido"] = (
    (df_cluster_merged["score_estacion_nombre"] >= 75)
    | df_cluster_merged["es_autovia"]
    | df_cluster_merged["es_autovia_geo"]
)


# Filtrar los no confiables
df_final = df_cluster_merged[df_cluster_merged["match_valido"]]


In [279]:
df_final[["cluster", "nombre_estacion_mejor", "score_estacion_nombre", "es_autovia"]].sort_values("score_estacion_nombre", ascending=False).head(10)


cluster                              nombre_estacion_mejor  \
795       797                                       estacion m30   
656       658                                       estacion m30   
766       768                      pte de andalucia gta cadiz eo   
741       743                                       estacion m30   
1356     1363                                       estacion m30   
722       724   tactico valle de oro rio de oro gta valle de oro   
710       712                                       estacion m30   
709       711                                       estacion m30   
673       675  arroyo fontarron arroyo fontarronfuente carran...   
655       657                                       estacion m30   

      score_estacion_nombre  es_autovia  
795                   100.0        True  
656                   100.0        True  
766                   100.0       False  
741                   100.0        True  
1356                  100.0        True  
722                   100.0       False  
710                   100.0        True  
709                   100.0        True  
673                   100.0       False  
655                   100.0        True

In [280]:
import re

def extraer_calles(nombre_estacion):
    if pd.isna(nombre_estacion):
        return []
    # Normaliza y extrae posibles nombres de calles
    nombre_estacion = nombre_estacion.lower()
    nombre_estacion = re.sub(r'[^\w\s]', '', nombre_estacion)  # eliminar signos
    palabras = nombre_estacion.split()
    return [p for p in palabras if len(p) > 3]  # nos quedamos con palabras útiles

def hay_coincidencia_calles(row):
    calles_cluster = row['localizacion_limpia']
    calles_estacion = extraer_calles(row['nombre_estacion_mejor'])
    
    if not isinstance(calles_cluster, list):
        return False

    return any(calle in ' '.join(calles_cluster).lower() for calle in calles_estacion)

df_cluster_merged['match_por_calle'] = df_cluster_merged.apply(hay_coincidencia_calles, axis=1)


In [281]:
df_cluster_merged['match_tipo'] = df_cluster_merged.apply(
    lambda row: 'por nombre' if row['score_estacion_nombre'] >= 75 else
                'autovia' if row['es_autovia'] else
                'por calle' if row['match_por_calle'] else
                'descartado',
    axis=1
)


In [282]:
df_cluster_merged['match_tipo'].value_counts()


match_tipo
por nombre    921
por calle     334
descartado    164
autovia        41
Name: count, dtype: int64

In [283]:
df_cluster_merged["match_tipo"] = df_cluster_merged.apply(
    lambda row: "por nombre" if row["score_estacion_nombre"] >= 75 else
                "autovia" if row["es_autovia"] else
                "descartado", axis=1
)

df_cluster_merged["match_tipo"].value_counts()


match_tipo
por nombre    921
descartado    498
autovia        41
Name: count, dtype: int64

### Juntar clusters por metros

In [284]:
from itertools import chain

def merge_clusters_por_distancia(df, lat_col="media_latitud", lon_col="media_longitud", distancia_m=20):
    # Convertir coordenadas a radianes
    coords = np.radians(df[[lat_col, lon_col]].values)
    tree = BallTree(coords, metric="haversine")
    radio = distancia_m / 6371000  # 6371 km es el radio de la tierra

    # Vecinos dentro del radio
    vecinos = tree.query_radius(coords, r=radio)

    # Agrupar conectados
    visitados = set()
    grupos = []

    for i, vecinos_i in enumerate(vecinos):
        if i in visitados:
            continue
        grupo = set(vecinos_i)
        cola = list(vecinos_i)
        while cola:
            j = cola.pop()
            if j not in visitados:
                visitados.add(j)
                nuevos = set(vecinos[j])
                if not nuevos.issubset(grupo):
                    cola.extend(nuevos - grupo)
                    grupo |= nuevos
        grupos.append(list(grupo))

    # Construir nuevo DataFrame fusionado
    fusionados = []
    for grupo in grupos:
        sub_df = df.iloc[grupo]

        if sub_df.empty:
            continue  # ❌ Evita el error: no hay nada que fusionar

        row = {
            "cluster_ids": sub_df["cluster"].tolist(),
            "media_latitud": sub_df[lat_col].mean(),
            "media_longitud": sub_df[lon_col].mean(),
            "localizacion_limpia": list(chain.from_iterable(sub_df["localizacion_limpia"])),
            "id_estacion_mejor": sub_df["id_estacion_mejor"].mode().iloc[0] if not sub_df["id_estacion_mejor"].mode().empty else None,
            "latitud_estacion_mejor": sub_df["latitud_estacion_mejor"].mean(),
            "longitud_estacion_mejor": sub_df["longitud_estacion_mejor"].mean(),
            "nombre_estacion_mejor": sub_df["nombre_estacion_mejor"].mode().iloc[0] if not sub_df["nombre_estacion_mejor"].mode().empty else None,
            "score_estacion_nombre": sub_df["score_estacion_nombre"].max()
        }

        fusionados.append(row)


    return pd.DataFrame(fusionados)


In [285]:
df_fusionado = merge_clusters_por_distancia(df_final, distancia_m=80)


In [286]:
# Filtrar por puntos cercanos a la M-30 y verl sus puntajes
df_m30 = df_cluster_merged[df_cluster_merged['score_estacion_vs_calles'] < 50]

# Mostrar los primeros registros con su puntaje
df_m30[['cluster', 'nombre_estacion_proxima', 'score_estacion_vs_calles', 'localizacion_limpia']].head(20)


cluster                            nombre_estacion_proxima  \
4         4          av. osa mayor o22 o e (araiz fco. sanfiz)   
6         6                              pruebas signals 99002   
7         7                              pruebas signals 99002   
8         8                              pruebas signals 99002   
9         9             arroyo pozuelo o e (via lactea humera)   
19       19                                                      
24       24  av. secundino zuazo julio cano lasso glorieta ...   
33       33                              pruebas signals 99001   
34       34  penagrande de bracamonte puentedey av. ensanch...   
41       41          san norberto e o(san tarsicio san erasmo)   
42       42                                                      
55       55  av. paraninfo s (juan del rosal facultad de de...   
56       56                                                      
59       59                    planeta av. general av. logrono   
62       62                    planeta av. general av. logrono   
64       64                    planeta av. general av. logrono   
65       65                    planeta av. general av. logrono   
68       68                                                      
73       73                   san jaime sierra tornavaca pilas   
76       76                          samaniego arcaute campezo   

    score_estacion_vs_calles  \
4                  48.275862   
6                  33.333333   
7                  41.025641   
8                  41.379310   
9                  44.444444   
19                  0.000000   
24                 45.238095   
33                 45.454545   
34                 45.000000   
41                 47.619048   
42                  0.000000   
55                 43.478261   
56                  0.000000   
59                 43.750000   
62                 46.153846   
64                 46.153846   
65                 45.283019   
68                  0.000000   
73                 46.666667   
76                 46.511628   

                                  localizacion_limpia  
4   [autov m autov a, avenida valdemarin call arge...  
6   [call suertes de la villa call mayorazgo de du...  
7   [call simpatia avenida miguel delibes, autov m...  
8   [call mario moreno cantinflas avenida miguel d...  
9   [call golondrina call rosas de aravaca, avenid...  
19  [autov m, autov m, ctra castilla s, autov m ki...  
24  [aerop terminal t ctra alcobendas a barajas, a...  
33  [call pirotecnia ctra madrid a rivas del jaram...  
34  [avenida mayorazgo autov m, avenida mayorazgo ...  
41  [call resina call san dalmacio, call resina, c...  
42  [autov a call allende, autov a s, call allende...  
55  [avenida complutense, avenida complutense call...  
56  [avenida niceto alcala zamora avenida francisc...  
59  [metro aeropuerto t t t, aerop terminal t, int...  
62  [aerop terminal t, parking t salidas, aerop te...  
64  [inter aeropuerto t t t p, inter aeropuerto t ...  
65  [aerop terminal t aerop terminal t, inter aero...  
68  [avenida cardenal herrera oria autov m, m30, a...  
73               [avenida mayorazgo call cincovillas]  
76  [call julio call diciembre, call julio, call a...

### ESTE ES SOLO PARA QUE SE VEA CUALES COGE Y CUALES NO, SOLO COGE LOS VERDES

In [287]:
import folium

# Crear el mapa centrado en el centroide general
centro_lat = df_cluster_merged["media_latitud"].mean()
centro_lon = df_cluster_merged["media_longitud"].mean()
m = folium.Map(location=[centro_lat, centro_lon], zoom_start=12)

# Función para asignar color por score
def get_color(score):
    if score >= 75:
        return "green"   # 🟢 Buen match
    elif score >= 50:
        return "orange"  # 🟡 Dudoso
    else:
        return "red"     # 🔴 Malo

# Añadir marcadores de clusters y sus estaciones
for _, row in df_cluster_merged.iterrows():
    color = get_color(row["score_estacion_vs_calles"])

    # Marcador del cluster (color según score)
    folium.CircleMarker(
        location=[row["media_latitud"], row["media_longitud"]],
        radius=5,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.9,
        popup=folium.Popup(f"""
            <b>Cluster:</b> {row["cluster"]}<br>
            <b>Estación:</b> {row["nombre_estacion_proxima"]}<br>
            <b>Score:</b> {row["score_estacion_vs_calles"]}
        """, max_width=300),
    ).add_to(m)

    # Marcador de la estación (verde fijo)
    folium.CircleMarker(
        location=[row["latitud_estacion"], row["longitud_estacion"]],
        radius=4,
        color="blue",
        fill=True,
        fill_color="blue",
        fill_opacity=0.5
    ).add_to(m)

    # Línea azul entre cluster y estación
    folium.PolyLine(
        locations=[
            [row["media_latitud"], row["media_longitud"]],
            [row["latitud_estacion"], row["longitud_estacion"]],
        ],
        color="blue",
        weight=1
    ).add_to(m)

# Mostrar el mapa
m


In [288]:
def debug_cluster(cluster_id):
    row = df_cluster_merged[df_cluster_merged["cluster"] == cluster_id]
    if row.empty:
        print("Cluster no encontrado.")
        return

    row = row.iloc[0]
    print(f"🔍 Cluster: {cluster_id}")
    print(f"📍 Coordenadas: {row['media_latitud']}, {row['media_longitud']}")
    print(f"🏷️  Estación asignada: {row['nombre_estacion_mejor']}")
    print(f"📊 Score: {row['score_estacion_nombre']}")
    print(f"🛣️ es_autovia: {row['es_autovia']}, es_autovia_geo: {row['es_autovia_geo']}")
    print(f"✅ match_valido: {row['match_valido']}")
    print("\n🚏 Calles en cluster:")
    for calle in row["localizacion_limpia"]:
        print(f" - {calle}")


In [289]:
debug_cluster(1304)



🔍 Cluster: 1304
📍 Coordenadas: 40.41371816151879, -3.661566622992417
🏷️  Estación asignada: estacion m30
📊 Score: 100.0
🛣️ es_autovia: True, es_autovia_geo: False
✅ match_valido: True

🚏 Calles en cluster:
 - m30
 - autov m calle
 - m30 lat


In [290]:
from scipy.spatial import cKDTree

# Crear árbol de búsqueda con estaciones
est_coords = df_estaciones[["latitud", "longitud"]].values
est_tree = cKDTree(est_coords)

# Coordenadas del cluster 657
lat_c, lon_c = 40.465477901483325, -3.66767003515749
dist, idxs = est_tree.query([lat_c, lon_c], k=5)  # las 5 más cercanas

# Mostrar nombres
df_estaciones.iloc[idxs][["id", "nombre", "latitud", "longitud"]]


id                                             nombre    latitud  \
1713  6719                                            PM20233  40.466529   
1712  6718                                            PM20232  40.466562   
3132  6717                                            PM20231  40.466521   
2170  6646                                            PM10211  40.466456   
4472  9984  Cta. Sagrados Corazones  - Sta. María Magdalen...  40.466725   

      longitud  
1713 -3.668062  
1712 -3.667961  
3132 -3.668244  
2170 -3.668430  
4472 -3.667427

### Este es el final que usamos

In [291]:
import folium

centro_lat = df_fusionado["media_latitud"].mean()
centro_lon = df_fusionado["media_longitud"].mean()
m = folium.Map(location=[centro_lat, centro_lon], zoom_start=12)

def get_color(score, es_autovia):
    if es_autovia:
        return "purple"  # todo lo detectado como autovía (por nombre)
    elif score >= 75:
        return "green"
    elif score >= 50:
        return "orange"
    else:
        return "gray"


for _, row in df_fusionado.iterrows():
    # Salta si hay coordenadas NaN
    if pd.isna(row["latitud_estacion_mejor"]) or pd.isna(row["longitud_estacion_mejor"]):
        continue

    color = get_color(row["score_estacion_nombre"], row.get("es_autovia", False))

    folium.CircleMarker(
        location=[row["media_latitud"], row["media_longitud"]],
        radius=5,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.9,
        popup=folium.Popup(f"""
            <b>Cluster:</b> {row["cluster_ids"]}<br>
            <b>Estación:</b> {row["nombre_estacion_mejor"]}<br>
            <b>Score:</b> {row["score_estacion_nombre"]}
        """, max_width=300)
    ).add_to(m)

    folium.CircleMarker(
        location=[row["latitud_estacion_mejor"], row["longitud_estacion_mejor"]],
        radius=4,
        color="blue",
        fill=True,
        fill_color="blue",
        fill_opacity=0.5,
        popup=folium.Popup(f"""
            <b>Estación vinculada:</b><br>
            {row['nombre_estacion_mejor'] if row['nombre_estacion_mejor'] else '(sin nombre)'}<br>
            <b>Score:</b> {row['score_estacion_nombre']}<br>
            <b>Cluster:</b> {row['cluster_ids']}
        """, max_width=300)
    ).add_to(m)


    folium.PolyLine(
        locations=[
            [row["media_latitud"], row["media_longitud"]],
            [row["latitud_estacion_mejor"], row["longitud_estacion_mejor"]]
        ],
        color="blue",
        weight=1
    ).add_to(m)


m


In [219]:
trafico_2024 = pd.read_csv('../trafico_2024_completo.csv', sep=";")

In [220]:
print(trafico_2024.head())

     id           fecha_hora tipo_elem  intensidad  ocupacion  carga  vmed  \
0  1001  2024-01-01 13:00:00       C30        1560        4.0      0  61.0   
1  1001  2024-01-01 13:15:00       C30        1728        4.0      0  60.0   
2  1001  2024-01-01 13:30:00       C30        1800        5.0      0  58.0   
3  1001  2024-01-01 13:45:00       C30        1704        5.0      0  58.0   
4  1001  2024-01-01 14:00:00       C30        1812        5.0      0  58.0   

  error  periodo_integracion   hora  mes trimestre    latitud  longitud  
0     N                    5  13:00    1        Q1  40.409729 -3.740786  
1     N                    5  13:15    1        Q1  40.409729 -3.740786  
2     N                    5  13:30    1        Q1  40.409729 -3.740786  
3     N                    5  13:45    1        Q1  40.409729 -3.740786  
4     N                    5  14:00    1        Q1  40.409729 -3.740786  


In [221]:
df_fusionado["num_elementos"] = df_fusionado["cluster_ids"].apply(len)


In [222]:
# Asegurar formato HH:MM y convertir a minutos desde medianoche
trafico_2024["hora"] = trafico_2024["hora"].astype(str).str[:5]
trafico_2024["hora_minutos"] = (
    trafico_2024["hora"].str.split(":").str[0].astype(int) * 60 +
    trafico_2024["hora"].str.split(":").str[1].astype(int)
)

# Si no tienes min_hora y max_hora, puedes usar todo el día:
min_hora_default = 0
max_hora_default = 1440

# Inicializar columna
df_fusionado["suma_intensidad"] = 0

# Recorrer cada cluster fusionado
for index, row in df_fusionado.iterrows():
    estacion = row["id_estacion_mejor"]
    
    filtro = (
        (trafico_2024["id"] == estacion) &
        (trafico_2024["hora_minutos"] >= min_hora_default) &
        (trafico_2024["hora_minutos"] <= max_hora_default)
    )

    suma = trafico_2024.loc[filtro, "intensidad"].sum()
    df_fusionado.at[index, "suma_intensidad"] = suma




In [223]:
# Calcular probabilidad
df_fusionado["probabilidad_accidente"] = df_fusionado["num_elementos"] / df_fusionado["suma_intensidad"].replace(0, np.nan)
df_fusionado

cluster_ids  media_latitud  media_longitud  \
0                   [0]      40.517878       -3.775513   
1                   [3]      40.353118       -3.570552   
2                  [12]      40.453450       -3.781125   
3                  [14]      40.464231       -3.784926   
4                  [15]      40.455044       -3.785334   
..                  ...            ...             ...   
983              [1459]      40.422442       -3.709335   
984              [1461]      40.421122       -3.692054   
985              [1462]      40.421958       -3.691818   
986  [1463, 1467, 1468]      40.419166       -3.693391   
987        [1464, 1465]      40.423100       -3.710387   

                                   localizacion_limpia  id_estacion_mejor  \
0    [ctra m30, call guardia civil, call m30 el rio...             3814.0   
1    [m30 servicio, lugar canada real frente no, lu...             5379.0   
2    [call arroyo de pozuelo, ctra humera call arro...             4874.0   
3    [cmno zarzuela call blanca de castilla, call l...            10108.0   
4    [calle golondrina calle brujula, call golondri...             4883.0   
..                                                 ...                ...   
983  [calle isabel la catolica, call gran via call ...             4290.0   
984     [paseo recoletos, paseo prado call villanueva]             4244.0   
985  [paseo recoletos call prim, paseo recoletos, p...             4244.0   
986  [paseo recoletos plaza cibeles, plaza cibeles ...             4246.0   
987  [plaza espana, call gran via, call gran via pl...             4292.0   

     latitud_estacion_mejor  longitud_estacion_mejor  \
0                 40.488349                -3.754235   
1                 40.364426                -3.598876   
2                 40.452493                -3.780809   
3                 40.462116                -3.783951   
4                 40.454831                -3.785388   
..                      ...                      ...   
983               40.421695                -3.709252   
984               40.421417                -3.692061   
985               40.421417                -3.692061   
986               40.419270                -3.694148   
987               40.423054                -3.710255   

                                 nombre_estacion_mejor  score_estacion_nombre  \
0    (tactico) ctra. el pardo s n(palacio de la zar...              85.714286   
1    canada santisimo av. ensanche de vallecas av. ...              53.012048   
2    arroyo pozuelo o98 e o (glorieta rio zancara h...              84.000000   
3                   pleyades o24 s(ardales ana teresa)              76.190476   
4       golondrina o22 s n (escultor peresejo brujula)              91.803279   
..                                                 ...                    ...   
983  isabel la catolica o e(pl. santo domingo gran ...              91.525424   
984                   po recoletos s(prim pl. cibeles)              75.000000   
985                   po recoletos s(prim pl. cibeles)              77.777778   
986                  alcala e o(pl. cibeles barquillo)              76.363636   
987                 gran via,78 s n (gral.mitre reyes)              76.190476   

     num_elementos  suma_intensidad  probabilidad_accidente  
0                1           801384            1.247841e-06  
1                1          2108401            4.742931e-07  
2                1          1992952            5.017682e-07  
3                1          1576124            6.344678e-07  
4                1          2193224            4.559498e-07  
..             ...              ...                     ...  
983              1          1784311            5.604404e-07  
984              1         13044367            7.666144e-08  
985              1         13044367            7.666144e-08  
986              3         14145583            2.120803e-07  
987              2          6927125            2.887201e-07  


In [121]:
# Ver top 10
top_10 = df_fusionado.nlargest(10, "probabilidad_accidente")
print(top_10)

      cluster_ids  media_latitud  media_longitud  \
588         [948]      40.451915       -3.686023   
25           [58]      40.483079       -3.649246   
188         [324]      40.419665       -3.619614   
9            [28]      40.483589       -3.616519   
594         [955]      40.443913       -3.691367   
613         [981]      40.445205       -3.691030   
131         [238]      40.389404       -3.757857   
402         [672]      40.393936       -3.739594   
758  [1234, 1235]      40.432084       -3.655592   
45           [97]      40.488716       -3.671631   

                                   localizacion_limpia  id_estacion_mejor  \
588  [call padre damian, plaza sagrados corazones, ...             3448.0   
25   [avenida niceto alcala zamora call pintor luci...            11105.0   
188  [avenida guadalajara call bulgaria, avenida gu...            11316.0   
9    [avenida juan antonio samaranch gta antonio pe...            11198.0   
594  [paseo castellana, paseo castellana c